# Big Data Analytics
Praktikum Sommersemester 2023. <small>Version 1.2</small>

**Aufgabe 2: Abfragen mit Apache Drill** 

Machen Sie sich mit Apache Drill vertraut. Lösen Sie die Aufgaben in `sqlline` oder in einem Jupyter Notebook. Nutzen Sie die markierten Zellen im vorliegenden Notebook `BDA1_A2_Drill` für die Lösung und laden Sie es in Ilias hoch.

----

## Vorbereitung
* Erzeugen Sie den Ordner `work/drill-driver` im JupyterLab Workspace
* Legen Sie eine neue Datei `odbc.ini` dort an. Sie finden ein Beispiel unter `Big_Data_Analytics_1/public/drill-driver/`


In Drill sind mehrere Datenmengen konfiguriert und für Sie verwendbar:

* **dfs.data.\`co2data.tsv\`**<br>DFS Datenquelle in Form eines Datensatz an Sensordaten
* **bdapi.labels**<br>HTTP Datenquelle mit Sensornamen und -Positionen
* **bdapi.sensors**<br>HTTP Datenquelle mit einer fixierten Liste von JSON Objekten mit Sensordaten.
* **bdapi.sensorslastday**<br>HTTP Datenqelle mit einem JSON Objekt, das dynamische Sensordaten anbietet.
* **weather.sunrise**<br>HTTP Storage einer API, die Zeiten des Sonnenauf- und Sonnenuntergangs an einer gegebenen Position (fields lat und lon) zu einem Datum (field date) zurückgibt. Mehr Infos dazu auf der Webseite zur [sunrise-sunset.org/api](https://sunrise-sunset.org/api).

## Verbindung zu Drill
-------------

In [1]:
import pyodbc
def connect(dsn='drill'):
    """opens the connection to given DSN"""
    conn = pyodbc.connect("DSN="+dsn, autocommit=True)
    if not conn.closed:
        print(f"connected to drillbit {dsn}")
        return conn
    else:
        print(f"could not connect to {dsn}")
        return None
    
con = connect()

query = '''SELECT version FROM sys.version'''
csr = con.cursor()

connected to drillbit drill


## Aufgabe 2 a

Verschaffen Sie sich einen Überblick über die Sensordaten, die Sie im Drill unter ``dfs.data.`co2data.tsv` `` finden. Beantworten Sie die folgenden
Fragen, indem Sie jeweils eine SQL-Query gegen das Drill Cluster ausführen:
    
1. Wieviele verschiedene Sensoren (angegeben im Feld _source_) enhält die Datenmenge?
2. Wieviele Datenpunkte je Sensor liegen vor? Geben Sie sowohl Sensor als auch Anzahl aus.
3. Bereiten Sie in einer SQL-Query die Werte in einzelnen Spalten so vor, dass sie sinnvolle Datentypen aufweisen:
    1. Sowohl _humidity_, _temperature_ als auch _co2_ sollen als auf zwei Nachkommastellen gerundete Fließkommazahlen verfügbar sein.
    2. Die erste Spalte gibt den Zeitstempel als Unix Epoch mit Mikrosekunden an. Machen Sie daraus einen Drill Timestamp
4. Was ist der höchste, und was der niedrigste Temperaturwert? Beide Werte sollen zusammen in einer Query angefragt werden. Kennzeichnen Sie die beiden Felder mit einem sprechenden Namen.
5. Was ist der durchschnittliche CO<sub>2</sub>-Wert je Sensor in der Datenmenge?


### Aufgabe 2a: 1. Anzahl der verschiedenen Sensoren
----------------
Bei der Auswahl der Werte wird die erste Zeile der Tabelle mit dem Schlüsselwort ``OFFSET`` übersprungen, da sie den Titel der Spalten enthält. <br>
Viele Werte kommen in der Tabelle doppelt vor aber wir brauchen nur die eindeutigen Werte für serial_number zu zählen, um die Anzahl der vorhandenen Sensoren zu ermitteln. Dazu verwenden wir das Schlüsselwort ``DISTINCT``.

In [2]:
# Aufgabe 2a: 1.

csr.execute("SELECT COUNT(DISTINCT columns[1]) AS anzahl_sensoren FROM (SELECT * FROM dfs.data.`co2data.tsv` OFFSET 1)")
result = csr.fetchone()
print("Anzahl der verschiedenen Sensoren: ", result.anzahl_sensoren)

Anzahl der verschiedenen Sensoren:  22


### Aufgabe 2a: 2. Anzahl der Datenpunkte je Sensor
----------------
**Idee**: Die Gesamtzahl der Messungen für jeden Sensor wird berechnet. <br>
Um die Summe zu erhalten, müssen die Daten aus der Spalte "measurement_count" zunächst mit ``CAST( .. AS INT)`` in INT umgewandelt werden und geprüft werden, ob ``ISNUMERIC( .. ) = 1`` ist, damit nur numerische Daten ausgewählt werden.

In [3]:
# Aufgabe 2a: 2.

csr.execute("SELECT COLUMNS[1] AS sensoren_serial_number, SUM(CAST(COLUMNS[0] AS INT)) AS sum_measurement_count FROM (SELECT * FROM dfs.data.`co2data.tsv` OFFSET 1) WHERE ISNUMERIC(COLUMNS[0]) = 1 GROUP BY COLUMNS[1]")
result = csr.fetchall()
column_names = [column[0] for column in csr.description]
print(column_names)
for row in result:
    print(row)

['sensoren_serial_number', 'sum_measurement_count']
('s_8caab57cc961_284337', 467495863402)
('s_e8db84c5f33d_', 2591530)
('s_8caab57a6dd9', 67469)
('s_8caab57cc961_', 1969626)
('s_3c6105d3abae_', 883829)
('s_10521c0202ab_284839', 853521)
('s_e8db84c5f33d', 1693)
('s_d8bfc0147061_283903', 145380488925)
('s_8caab57a6dd9_', 472212)
('s_d8bfc014724e_262793', 1557235314035)
('s_8caab57a6dd9_0xdeadbeef', 1176)
('s_10521c01cf19_', 467316)
('s_e8db84c5f771_300390', 460673265336)
('s_e8db84c5f33d_0xdeadbeef', 1001704)
('s_e8db84c5f771_', 165924)
('s_3c6105d3abae_299589', 1100374836812)
('s_8caab57c3e19_', 1212530)
('s_8caab57a6dd9_288065', 550011461054)
('s_10521c01cf19_262520', 105903540456)
('s_8caab57c3e19_282028', 780597588352)
('s_e8db84c5f33d_281913', 523839626443)
('s_d8bfc0147061_', 129273)


### Aufgabe 2a: 3. Werte in verschiedenen Datentypen ausgeben
----------------
Die Werte für "humidity", "temperature" und "co2" werden in double mit einer Genauigkeit von 32 und 2 Nachkommastellen umgewandelt (``CAST ( .. AS DOUBLE(32,2))``), wobei die Werte von "timestamp" zunächst in int umgewandelt werden, dann im Format eines Drill Timestamps angezeigt wird. (``TO_TIMESTAMP( .. )``)

In [4]:
# Aufgabe 2a: 3.

csr.execute("SELECT CAST(COLUMNS[5] AS DECIMAL(32,2)) as humidity, CAST(COLUMNS[4] AS DECIMAL(32,2)) as temperature, CAST(COLUMNS[3] AS DECIMAL(32,2)) as co2, TO_TIMESTAMP(CAST(COLUMNS[6] AS INT)) as time_stamp FROM dfs.data.`co2data.tsv` WHERE ISNUMERIC(COLUMNS[6]) = 1 AND ISNUMERIC(COLUMNS[5]) = 1 AND ISNUMERIC(COLUMNS[4]) = 1 AND ISNUMERIC(COLUMNS[3]) = 1")
result = csr.fetchall()
column_names = [column[0] for column in csr.description]
print(column_names)
for row in result:
    print(row)

['humidity', 'temperature', 'co2', 'time_stamp']
(Decimal('36.00'), Decimal('23.00'), Decimal('420.00'), datetime.datetime(2021, 4, 1, 12, 8, 48))
(Decimal('32.00'), Decimal('24.00'), Decimal('421.00'), datetime.datetime(2021, 4, 1, 12, 8, 56))
(Decimal('32.00'), Decimal('24.00'), Decimal('420.00'), datetime.datetime(2021, 4, 1, 12, 8, 59))
(Decimal('44.00'), Decimal('20.00'), Decimal('651.00'), datetime.datetime(2021, 4, 1, 12, 9, 21))
(Decimal('36.00'), Decimal('23.00'), Decimal('422.00'), datetime.datetime(2021, 4, 1, 12, 9, 29))
(Decimal('36.00'), Decimal('23.00'), Decimal('422.00'), datetime.datetime(2021, 4, 1, 12, 9, 32))
(Decimal('36.00'), Decimal('23.00'), Decimal('423.00'), datetime.datetime(2021, 4, 1, 12, 9, 39))
(Decimal('41.00'), Decimal('22.00'), Decimal('436.00'), datetime.datetime(2021, 4, 1, 12, 9, 47))
(Decimal('44.00'), Decimal('20.00'), Decimal('653.00'), datetime.datetime(2021, 4, 1, 12, 10, 1))
(Decimal('44.00'), Decimal('20.00'), Decimal('653.00'), datetime.date

### Aufgabe 2a: 4. Höchste und niedrigste Temperaturwerte ausgeben 
----------------
Die Funktionen ``MIN()`` und ``MAX()`` nehmen nur numerische Werte als Parameter an, daher müssen die Temperaturwerte zuerst in int umgewandelt werden. 

In [5]:
# Aufgabe 2a: 4.

csr.execute("SELECT MAX(CAST(COLUMNS[4] AS FLOAT)) AS highest_temperature, MIN(CAST(COLUMNS[4] AS FLOAT)) AS lowest_temperature FROM dfs.data.`co2data.tsv` WHERE ISNUMERIC(COLUMNS[4]) = 1")
result = csr.fetchall()
column_names = [column[0] for column in csr.description]
print(column_names)
for row in result:
    print(row)

['highest_temperature', 'lowest_temperature']
(36.0, -1.0)


### Aufgabe 2a: 5. Durchschnittlicher CO2-Wert
------------------
Die Funktion ``AVG()`` nimmt auch nur numerische Werte als Parameter an, daher müssen die CO2-Werte zuerst in int umgewandelt werden. 

In [6]:
# Aufgabe 2a: 5.
 
csr.execute("SELECT COLUMNS[1] AS sensoren, AVG(CAST(COLUMNS[3] AS INT)) AS average_CO2 FROM dfs.data.`co2data.tsv` WHERE ISNUMERIC(COLUMNS[3]) = 1 GROUP BY COLUMNS[1]")
result = csr.fetchall()
column_names = [column[0] for column in csr.description]
print(column_names)
for row in result:
    print(row)

['sensoren', 'average_CO2']
('s_8caab57cc961_284337', 470.7930161035675)
('s_e8db84c5f33d_', 488.7692307692308)
('s_8caab57cc961_', 429.2857142857143)
('s_3c6105d3abae_', 832.0)
('s_10521c0202ab_284839', 436.76356589147287)
('s_e8db84c5f33d', 1403.2289156626507)
('s_d8bfc0147061_283903', 628.6339168406931)
('s_8caab57a6dd9_', 983.6666666666666)
('s_d8bfc014724e_262793', 770.4554948583827)
('s_8caab57a6dd9_0xdeadbeef', -1.0)
('s_10521c01cf19_', 467.5)
('s_e8db84c5f771_300390', 954.0877634759553)
('s_e8db84c5f33d_0xdeadbeef', -1.0)
('s_e8db84c5f771_', 863.0)
('s_3c6105d3abae_299589', 833.9766714887442)
('s_8caab57c3e19_', 620.0)
('s_8caab57a6dd9_288065', 654.238815923578)
('s_10521c01cf19_262520', 500.67781606479303)
('s_8caab57c3e19_282028', 876.9315842912921)
('s_e8db84c5f33d_281913', 531.2104615783285)
('s_d8bfc0147061_', 722.0)


## Aufgabe 2 b

1. Verknüpfen Sie die Daten aus ``dfs.data.`co2data.tsv` ``  mit den Daten aus `bdapi.labels`. Geben Sie, wenn möglich, den Sensornamen ( _name_ ) und Besitzer ( _owner_ ) zu jeder Seriennummer aus. Falls Daten fehlen, geben Sie die Seriennummer dennoch aus.<br>Hinweis: Die Seriennummern liegen bei den beiden Datenmengen in unterschiedlicher Repräsentation vor. Untersuchen Sie die Datenmengen und ändern Sie Ihre Query so ab, dass die Seriennummern korrekt verknüpft werden. 
2. Überführen Sie diese Query (aus 2b) 1) in eine View. Sie haben Schreibrecht im Workspace `dfs.tmp`. Legen Sie darin eine View namens `labels_<ihre Ilias-ID>` an.<br>Beispiel: Lautet Ihre Ilias-ID `mr1337s` nutzen Sie `labels_mr1337s`. Falls diese View bereits existiert soll sie überschrieben werden!
3. Nutzen Sie Ihre neu angelegte View nun und zeigen Sie alle Sensoren des Besitzers `Elsen` an.
4. Wann ein Sensor eines unbekannten Besitzers (`unknown`) zum ersten Mal gesendet?
5. Lassen Sie sich den physischen Plan für die Query aus 2b 4. anzeigen. 

### Aufgabe 2b: 1. Daten aus zwei Dateien verknüpfen
------------------
**Idee**: Die auszugebenden Datenspalten auswählen und nach Ähnlichkeiten zwischen den beiden Tabellen finden, um sie zu vereinigen. <br>
In dieser Aufgabe sind die Seriennummern der Sensoren, die verbunden werden können aber die Seriennummern liegen bei den beiden Datenmengen in unterschiedlicher Repräsentation vor. <br>
Beispiel:
- Seriennummer in ``dfs.data.`co2data.tsv` ``: s_e8db84c5f33d_281913
- Seriennummer in `bdapi.labels`: E8DB84C5F33D <br>
<br>Die Seriennummer aus *dfs.data.co2data.tsv* wird zunächst mit ``SPLIT_PART(.. , '_' ,2)`` aufgeteilt und gibt die Werte zwischen den beiden Unterstrichen als Substring zurück. <br>
Die Zeichenkette wird dann mit ``UPPER(...)`` in Großbuchstaben umgewandelt, so dass sie mit den Werten in *bdapi.labels* übereinstimmt.

In [7]:
# Aufgabe 2b: 1.

csr.execute("SELECT c.serial_number, c.datetime, l.name, l.owner FROM (SELECT CAST(columns[1] AS VARCHAR) AS serial_number, CAST(columns[6] AS INT) AS datetime FROM dfs.data.`co2data.tsv` WHERE columns[1] <> 'serial_number' AND columns[1] <> 'null') AS c LEFT JOIN bdapi.labels AS l ON UPPER(SPLIT_PART(c.serial_number, '_', 2))=l.serial")
result = csr.fetchall()
column_names = [column[0] for column in csr.description]
print(column_names)
for row in result:
    print(row)

['serial_number', 'datetime', 'name', 'owner']
('s_d8bfc014724e_262793', 1617271728, 'Main Station S1', 'Elsen')
('s_10521c0202ab_284839', 1617271736, 'Main Station S4', 'Elsen')
('s_10521c0202ab_284839', 1617271739, 'Main Station S4', 'Elsen')
('s_e8db84c5f771_300390', 1617271761, 'Commerce Center S7', 'Unknown')
('s_d8bfc014724e_262793', 1617271769, 'Main Station S1', 'Elsen')
('s_d8bfc014724e_262793', 1617271772, 'Main Station S1', 'Elsen')
('s_d8bfc014724e_262793', 1617271779, 'Main Station S1', 'Elsen')
('s_8caab57c3e19_282028', 1617271787, 'Main Station S2', 'Elsen')
('s_e8db84c5f771_300390', 1617271801, 'Commerce Center S7', 'Unknown')
('s_e8db84c5f771_300390', 1617271806, 'Commerce Center S7', 'Unknown')
('s_e8db84c5f771_300390', 1617271813, 'Commerce Center S7', 'Unknown')
('s_8caab57c3e19_282028', 1617271831, 'Main Station S2', 'Elsen')
('s_e8db84c5f33d_281913', 1617271840, 'Commerce Center S6', 'Unknown')
('s_e8db84c5f33d_281913', 1617271843, 'Commerce Center S6', 'Unknown')

### Aufgabe 2b: 2. View anlegen
------------------
Eine neue View anlegen, falls sie bereits existiert, wird sie ersetzt und die Query aus der vorherigen Aufgabe in die View überführt.

In [8]:
# Aufgabe 2b: 2.

csr.execute("CREATE OR REPLACE VIEW dfs.tmp.labels_pl5146s AS SELECT c.serial_number, c.datetime, l.name, l.owner FROM (SELECT CAST(columns[1] AS VARCHAR) AS serial_number, columns[6] AS datetime FROM dfs.data.`co2data.tsv` WHERE columns[1] <> 'serial_number' AND columns[1] <> 'null') AS c LEFT JOIN bdapi.labels AS l ON UPPER(SPLIT_PART(c.serial_number, '_', 2))=l.serial")
result = csr.fetchall()
column_names = [column[0] for column in csr.description]
print(column_names)
for row in result:
    print(row)

['ok', 'summary']
(True, "View 'labels_pl5146s' replaced successfully in 'dfs.tmp' schema")


### Aufgabe 2b: 3. Alle Sensoren des Besitzers Elsen anzeigen
------------------

In [9]:
# Aufgabe 2b: 3.

csr.execute("SELECT * FROM dfs.tmp.labels_pl5146s WHERE owner = 'Elsen'")
result = csr.fetchall()
column_names = [column[0] for column in csr.description]
print(column_names)
for row in result:
    print(row)

['serial_number', 'datetime', 'name', 'owner']
('s_d8bfc014724e_262793', '1617271728', 'Main Station S1', 'Elsen')
('s_10521c0202ab_284839', '1617271736', 'Main Station S4', 'Elsen')
('s_10521c0202ab_284839', '1617271739', 'Main Station S4', 'Elsen')
('s_d8bfc014724e_262793', '1617271769', 'Main Station S1', 'Elsen')
('s_d8bfc014724e_262793', '1617271772', 'Main Station S1', 'Elsen')
('s_d8bfc014724e_262793', '1617271779', 'Main Station S1', 'Elsen')
('s_8caab57c3e19_282028', '1617271787', 'Main Station S2', 'Elsen')
('s_8caab57c3e19_282028', '1617271831', 'Main Station S2', 'Elsen')
('s_d8bfc014724e_262793', '1617271859', 'Main Station S1', 'Elsen')
('s_8caab57c3e19_282028', '1617271873', 'Main Station S2', 'Elsen')
('s_8caab57c3e19_282028', '1617271876', 'Main Station S2', 'Elsen')
('s_8caab57c3e19_282028', '1617271883', 'Main Station S2', 'Elsen')
('s_8caab57c3e19_282028', '1617271886', 'Main Station S2', 'Elsen')
('s_8caab57c3e19_282028', '1617271891', 'Main Station S2', 'Elsen')
(

### Aufgabe 2b: 4. Wann ein Sensor eines unbekannten Besitzers zum ersten Mal gesendet?
-------------------
**Idee**: Beim ersten Senden bedeutet, dass der Wert von datetime der niedrigste ist. <br>
Da die Funktion ``MIN()`` nur numerische Werte als Parameter annimmt, die Werte von datetime müssen zuerst in int umgewandelt werden. <br>
datetime mit "null" als Wert wird nicht berücksichtigt. ( ``WHERE datetime <> 'null' `` )

In [10]:
# Aufgabe 2b: 4.

csr.execute("SELECT MIN(CAST(datetime AS INT)) AS first_sent_date FROM dfs.tmp.labels_pl5146s WHERE datetime <> 'null' AND owner = 'Unknown'")
result = csr.fetchone()
column_names = [column[0] for column in csr.description]
print(column_names)
print(result)

['first_sent_date']
(1617097805, )


### Aufgabe 2b: 5. Einen physischen Plan
------------
**Definition:** <br>
Ein physischer Plan ist eine Reihe von Anweisungen, die beschreiben, wie eine Abfrage oder eine DML-Anweisung (Data Manipulation Language) in SQL Server ausgeführt wird.
 <br> <br>
``EXPLAIN PLAN``-Anweisung zeigt die vom Optimierer ausgewählten Ausführungspläne für SELECT-, UPDATE-, INSERT- und DELETE-Anweisungen an. 

In [11]:
# Aufgabe 2b: 5.
csr.execute("EXPLAIN PLAN FOR SELECT MIN(CAST(datetime AS FLOAT)) AS first_sent_date FROM dfs.tmp.labels_pl5146s WHERE datetime <> 'null' AND owner = 'Unknown'")
result = csr.fetchall()
column_names = [column[0] for column in csr.description]
print(column_names)
for row in result:
    print(row)

['text', 'json']
('00-00    Screen\n00-01      Project(first_sent_date=[$0])\n00-02        ComplexToJson\n00-03          Project(first_sent_date=[$0])\n00-04            StreamAgg(group=[{}], first_sent_date=[MIN($0)])\n00-05              StreamAgg(group=[{}], first_sent_date=[MIN($0)])\n00-06                Project($f0=[CAST($0):FLOAT])\n00-07                  HashJoin(condition=[=($1, $2)], joinType=[inner], semi-join: =[false])\n00-09                    Project(datetime=[$1], $f2=[UPPER(SPLIT_PART(CAST($0):VARCHAR(65535), \'_\', 2))])\n00-11                      SelectionVectorRemover\n00-13                        Filter(condition=[AND(<>($0, \'serial_number\'), <>($0, \'null\'), <>($1, \'null\'))])\n00-14                          Project(ITEM=[ITEM($0, 1)], ITEM1=[ITEM($0, 6)])\n00-15                            Scan(table=[[dfs, data, co2data.tsv]], groupscan=[EasyGroupScan [selectionRoot=file:/opt/data/bda1/co2data.tsv, numFiles=1, columns=[`columns`[1], `columns`[6]], files=[file:

## Aufgabe 2 c

1. Die Datenmenge unter `dfs.bdapi.sensorslastday` ändert sich in Intervallen.  Finden Sie einen Weg, diese Datenmenge nutzbar zu machen. (Tipp: Drill bietet Funktionen für komplexe Datentypen an, z.B. [FLATTEN()](https://drill.apache.org/docs/flatten/)). Die Antwort Ihrer Query sollte die Felder `timewindow`, `celsius` und `humidity` liefern.
2. Geben Sie mit einer einzigen Query die beiden Datenpunkte der extremen Temperaturen (`celsius`) aus, d.h. die Zeile mit der höchsten Temeperatur und die Zeile mit der niedrigsten Temperatur.
3. Optional: Finden Sie für die Datenmenge `dfs.bdapi.sensorslastday` zu jedem Zeitraum heraus, ob es Tag ist oder Nacht. Das können Sie mithilfe der Datenmenge `dfs.weather.sunrise` tun. Nehmen Sie für den Sensor in der Datenmenge die Geokoordinaten `50.75410842895508`, `6.08587121963501` an.  

### Aufgabe 2c: 1. FLATTEN()
-------------
``FLATTEN()`` teilt die Elemente in einzelne Datensätze auf. <br>
**Implementierung:** <br>
- ``FLATTEN(resultset) AS a`` - dient dazu, das Feld resultset aus der Tabelle bdapi.sensorslastday zu flatten <br>
&nbsp;&nbsp;&nbsp;(alle Werte in resultset werden in separate Zeilen umgewandelt)
- Die innerste Abfrage wird als b in der äußeren Abfrage verwendet, um auf die Ergebnisse der inneren Abfrage zu verweisen.
- In der äußeren Abfrage werden die gewünschten Spalten timewindow, celsius und humidity aus der flattenierten Spalte a der inneren Abfrage ausgewählt und mit Aliasnamen versehen (``b.a.timewindow AS timewindow, b.a.celsius AS celsius, b.a.humidity AS humidity``).

In [12]:
# Aufgabe 2c: 1.

csr.execute("SELECT b.a.timewindow AS timewindow, b.a.celsius AS celsius, b.a.humidity AS humidity FROM (SELECT FLATTEN(resultset) AS a FROM bdapi.sensorslastday) AS b")
result = csr.fetchall()
column_names = [column[0] for column in csr.description]
print(column_names)
for row in result:
    print(row)

['timewindow', 'celsius', 'humidity']
('2023-05-25 01:45:00', 20.4569664001, 38.3745994568)
('2023-05-25 01:45:00', 23.2906246185, 32.8892478943)
('2023-05-25 01:30:00', 20.5134760539, 38.4232215881)
('2023-05-25 01:30:00', 23.3342444102, 32.8158798218)
('2023-05-25 01:15:00', 23.3813152313, 32.7645161947)
('2023-05-25 01:15:00', 20.5992183685, 38.3988812764)
('2023-05-25 01:00:00', 20.6258792877, 37.87150383)
('2023-05-25 01:00:00', 23.4249343872, 32.6618016561)
('2023-05-25 00:45:00', 20.6678390503, 38.3801930745)
('2023-05-25 00:45:00', 23.4686196645, 32.5205574036)
('2023-05-25 00:30:00', 23.5156898499, 32.482035319)
('2023-05-25 00:30:00', 20.7330080668, 38.1894518534)
('2023-05-25 00:15:00', 20.7998695374, 38.0473073324)
('2023-05-25 00:15:00', 23.5777994792, 32.2453893026)
('2023-05-25 00:00:00', 20.8633460999, 37.9930725098)
('2023-05-25 00:00:00', 23.6264972687, 32.1793454488)
('2023-05-24 23:45:00', 23.6853510539, 32.0252399445)
('2023-05-24 23:45:00', 20.9319006602, 38.02673

### Aufgabe 2c: 2. Zeile mit der höchsten Temeperatur und mit der niedrigsten Temperatur
---------------
**Implementierung:**
- ``SELECT FLATTEN(resultset) AS data FROM bdapi.sensorslastday`` dient dazu, resultset aus der Tabelle bdapi.sensorslastday zu flatten
-``WHERE`` vergleicht den Wert von der Spalte celsius in den flachgestellten Daten (a.data) mit dem maximalen (``MAX(a.data.celsius)``) und dem minimalen (``MIN(a.data.celsius)``) Wert der Temperatur in der Tabelle. <br>
Dadurch werden nur die Zeilen ausgewählt, deren Temperatur entweder das Maximum oder das Minimum ist.
- Ergebnis: alle Spalten von den Zeilen mit den höchsten und niedrigsten Temperaturen werden angezeigt 

In [13]:
# Aufgabe 2c: 2.

csr.execute("SELECT * FROM (SELECT FLATTEN(resultset) AS data FROM bdapi.sensorslastday) AS a WHERE a.data.celsius = (SELECT MAX(a.data.celsius) FROM (SELECT FLATTEN(resultset) AS data FROM bdapi.sensorslastday) AS a) OR a.data.celsius = (SELECT MIN(a.data.celsius) FROM (SELECT FLATTEN(resultset) AS data FROM bdapi.sensorslastday) AS a)")
result = csr.fetchall()
print(column_names)
for row in result:
    print(row)

['timewindow', 'celsius', 'humidity']
('{\n  "timewindow" : "2023-05-21 01:45:00",\n  "celsius" : -34.4796854655,\n  "source" : "0013A20041A2F852",\n  "humidity" : 37.5067532857,\n  "pressure" : 958.871887207,\n  "room" : "H217"\n}', )
('{\n  "timewindow" : "2023-05-20 14:30:00",\n  "celsius" : 27.9635416667,\n  "source" : "0013A20041A7859A",\n  "humidity" : 29.1601657867,\n  "pressure" : 951.5822753906,\n  "room" : "H216"\n}', )


In [14]:
# Aufabe 2c: 3. optional

_____